# Identifier les coordonnées GPS à partir des pixels d'une image

Le but : filtrer les zones éligibles à l'installation d'éoliennes. Les données étant trop lourdes à visualiser, nous allons essayer de déterminer les coordonnées à partir des pixels pour ne charger qu'un array à la fin.

Pour que le code fonctionne, faire un screenshot de la carte en plaçant une ville repère 1 dans le coin supérieur gauche et une ville repère 2 dans le coin inférieur droit.
Ensuite préciser les coordonnées de ces villes dans les constantes `city_top_left` et `city_bottom_right`. (Clic droit sur la ville dans Google Maps pour copier les coordonnées)

In [1]:
import json
import os
from PIL import Image
import numpy as np
import pandas as pd
import plotly.express as px

Les constantes correspondent aux enjeux.

Utiliser les images du dossier `src/maps`, qui contiennent les infos de couleurs ainsi que les villes repères pour déterminer les coordonnées.

In [2]:
COLOR_FILTERS = [(128, 0, 128), (206, 136, 255)]

In [3]:
def get_gps_coordinates(x: int, y: int, width: int, height: int,
                        lat1: float, lon1: float, lat2: float, lon2: float,
                        lon_compression_coeff: float = 1,
                        lat_compression_coeff: float = 1
                        ) -> tuple[float, float]:
    """
    Calcule les coordonnees GPS pour un pixel donné.
    
    x, y : Position du pixel dans l'image
    width, height : Dimensions de l'image
    lat1, lon1 : Coordonnees GPS du coin superieur gauche
    lat2, lon2 : Coordonnees GPS du coin inférieur droit
    """
    latitude = lat1 + (y / height) * (lat2 - lat1) * lat_compression_coeff
    longitude = lon1 + (x / width) * (lon2 - lon1) * lon_compression_coeff

    return latitude, longitude


coordinates_list = []
for i in range(1, 4):  # nb images
    img_file = f"../src/maps/{i}.png"
    json_file = f"../src/maps/{i}.geojson"
    if not os.path.isfile(img_file) or not os.path.isfile(json_file):
        continue

    print(i)
    # load image
    image = np.array(Image.open(img_file))

    height, width, _ = image.shape

    # load json
    with open(json_file) as f:
        gj = json.load(f)

    # get cities
    lon1, lat1 = gj["features"][0]["geometry"]["coordinates"]
    lon2, lat2 = gj["features"][1]["geometry"]["coordinates"]

    # find coordinates
    for y in range(height):
        for x in range(width):
            for color in COLOR_FILTERS:
                try:
                    if np.array_equal(image[y, x][:3], color):  # [:3] skip alpha
                        lat, lon = get_gps_coordinates(x, y,
                                                    width, height,
                                                    lat1, lon1,
                                                    lat2, lon2)

                        color = f"rgb({color[0]},{color[1]},{color[2]})"

                        coordinates_list.append([lat, lon, color])

                except Exception as e:
                    pass  # n'arrive pas a calculer car len = len-1 je crois


# build dataframe
df = pd.DataFrame(coordinates_list, columns=["LAT", "LON", "Color"])
df.head()

fig = px.scatter_mapbox(df, lat="LAT", lon="LON",
                        color="Color",
                        zoom=5,
                        height=800)


fig.update_layout(mapbox_style="open-street-map")
fig.show()

1
2
3


In [4]:
df.shape

(71457, 3)

In [5]:
df.head()

LAT       LON             Color
0  50.672033  2.247981  rgb(206,136,255)
1  50.672033  2.255190  rgb(206,136,255)
2  50.667297  2.247981  rgb(206,136,255)
3  50.667297  2.255190  rgb(206,136,255)
4  50.624672  2.161480  rgb(206,136,255)

In [6]:
df.to_csv("zones_02.csv", index=False)